In [496]:
import matplotlib.pyplot as plt
from e3nn import o3, io, nn
import numpy as np
import torch 
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
import open3d as o3d
import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from functools import partial, reduce

In [497]:
from data_generation import SimpleShapeDataset

dataset = SimpleShapeDataset(sample_points=10000)

data = next(iter(DataLoader(dataset, batch_size=1))).float()

In [498]:
# how does it look like in spherical harmonics?

sphten = io.SphericalTensor(10, 1, 1)
signal = o3.spherical_harmonics(sphten, x=data, normalize=False).sum(dim=[0, 1])

fig = make_subplots(rows=1, cols=2, specs=[[{'is_3d': True} for j in range(2)] for i in range(1)])
fig.add_trace(go.Scatter3d(x=data[0, :, 0], y=data[0, :, 1], z=data[0, :, 2]), row=1, col=1)
fig.add_trace(go.Surface(sphten.plotly_surface(signal, radius=True)[0]), row=1, col=2)

In [409]:
class EncoderDecoder(nn.Module):
    def __init__(self):
        super(EncoderDecoder, self).__init__()
        
        # todo later reduce the irreps used but for now add as much as you can to make sure the thing works...
        lmax = 7
        # self.irreps_sh = reduce(lambda x, y: x + y, [e3nn.io.SphericalTensor(lmax=lmax, p_arg=a, p_val=b) for a in [-1, 1] for b in [-1, 1]])
        self.irreps_sh = io.SphericalTensor(lmax=lmax, p_arg=1, p_val=1) # todo should we have odd irreps as well?
        self.irreps_sh.sort()
        self.irreps_sh = self.irreps_sh.simplify()
        print('irreps:', self.irreps_sh)


    def forward(self, x):
        pass
    # def forward(self, data) -> torch.Tensor:
    #     num_neighbors = 2  # typical number of neighbors
    #     num_nodes = 4  # typical number of nodes
    # 
    #     edge_src, edge_dst = radius_graph(x=data.pos, r=1.1, batch=data.batch)  # tensors of indices representing the graph
    #     edge_vec = data.pos[edge_src] - data.pos[edge_dst]
    #     edge_sh = o3.spherical_harmonics(
    #         l=self.irreps_sh,
    #         x=edge_vec,
    #         normalize=False,  # here we don't normalize otherwise it would not be a polynomial
    #         normalization="component",
    #     )
    # 
    #     # For each node, the initial features are the sum of the spherical harmonics of the neighbors
    #     node_features = scatter(edge_sh, edge_dst, dim=0).div(num_neighbors**0.5)
    # 
    #     # For each edge, tensor product the features on the source node with the spherical harmonics
    #     edge_features = self.tp1(node_features[edge_src], edge_sh)
    #     node_features = scatter(edge_features, edge_dst, dim=0).div(num_neighbors**0.5)
    # 
    #     edge_features = self.tp2(node_features[edge_src], edge_sh)
    #     node_features = scatter(edge_features, edge_dst, dim=0).div(num_neighbors**0.5)
    # 
    #     # For each graph, all the node's features are summed
    #     return scatter(node_features, data.batch, dim=0).div(num_nodes**0.5)

EncoderDecoder()

irreps: 1x0e+1x1e+1x2e+1x3e+1x4e+1x5e+1x6e+1x7e


EncoderDecoder()

In [410]:
# e3nn.o3.spherical_harmonics(irreps
# )

torch.round(
    e3nn.o3.Irrep('1e').D_from_axis_angle(-torch.tensor([[1.1341, 2.23, -1.2452]]), torch.tensor([np.pi/2 * 0.924])),
    decimals=2)

tensor([[[ 0.2600, -0.1600, -0.9500],
         [ 0.7300,  0.6800,  0.0900],
         [ 0.6300, -0.7200,  0.2900]]])

In [411]:
sample_rot = torch.tensor([[[ 0.2600, -0.1600, -0.9500],
         [ 0.7300,  0.6800,  0.0900],
         [ 0.6300, -0.7200,  0.2900]]])

torch.round(
    e3nn.o3.Irrep('0e').D_from_matrix(torch.eye(3)),
    decimals=2)

tensor([[1.]])

In [412]:
-e3nn.o3.rand_matrix()

tensor([[-0.5714, -0.1041,  0.8141],
        [ 0.4865,  0.7559,  0.4381],
        [ 0.6610, -0.6463,  0.3813]])

In [413]:
o3.Irreps.spherical_harmonics(5)

1x0e+1x1o+1x2e+1x3o+1x4e+1x5o

In [414]:
# irreps = o3.Irreps.spherical_harmonics(3)
# irreps = io.SphericalTensor(10, 1, -1)


X = torch.tensor([1])
Y = torch.tensor([-1.03])
Z = torch.tensor([1])
vec = torch.cat([X, Y, Z]).float() # strange ordering that e3nn requires...

x = o3.spherical_harmonics(
    l=3,
    x=vec,
    normalize=True,
    normalization="component"
)

x

# go.Figure([go.Surface(irreps.plotly_surface(x, radius=False)[0])])

tensor([ 0.7812, -1.9709,  0.6788,  0.9868,  0.6788, -0.0000, -0.7812])

In [415]:
sphten = io.SphericalTensor(1, 1, 1)
o3.spherical_harmonics(sphten, x=torch.tensor([1, 0, 0]), normalize=False)

tensor([0.2821, 0.4886, 0.0000, 0.0000])

In [357]:
sphten = io.SphericalTensor(11, 1, -1)
signal = o3.spherical_harmonics(sphten, x=torch.tensor([1, 0, 0]), normalize=False)
            # o3.spherical_harmonics(sphten, x=torch.tensor([0, 1, 0]), normalize=False)

signal = signal / signal[0]

print(signal[:4])

go.Figure([go.Surface(sphten.plotly_surface(signal, radius=False)[0])])

tensor([1.0000, 1.7321, 0.0000, 0.0000])


In [254]:
o3.spherical_harmonics(o3.Irreps('0e'), torch.randn(2, 3), True, normalization='component')

tensor([[1.],
        [1.]])

In [177]:
irreps

1x0e+1x1o+1x2e+1x3o

In [166]:
r = o3.s2_grid(10, 10)

o3.plot(r)


p_val = 1
p_arg = 1
sphten = io.SphericalTensor(3, p_val, p_arg)
go.Figure([go.Surface(sphten.plotly_surface(images_on_s2, radius=False)[0])])

AttributeError: module 'e3nn.o3' has no attribute 'plot'